In [99]:
from pathlib import Path
import json
from cogent3 import get_app
def find_subdirectory_paths(root_dir):
    root_path = Path(root_dir)
    subdirectory_paths = {}
    # Iterate over each item in the root directory
    for item in root_path.iterdir():
        if item.is_dir():  # Check if the item is a directory
            folder_name = item.name
            subdirectory_paths[folder_name] = str(item)

    return subdirectory_paths

import os
from scipy import stats

import numpy as np
from plotly.subplots import make_subplots

import plotly.graph_objects as go
from clock_project.simulation.magnitude_quantification import calculate_non_stationarity, calculate_ENS, random_nucleotide_distribution, calculate_information, entropy_calculation

# model_fit_result_path = '/Users/gulugulu/repos/PuningAnalysis/results/output_data/model_fitting_result/ENSG00000127125.json'
# load_json_app = get_app("load_json")
# result_lf = load_json_app(model_fit_result_path)
# ens_tree = result_lf.get_ens_tree()
# ens_tree.get_figure(show_support=True, threshold=0.8, height = 1500, width = 1000)



In [314]:
path = '/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/triads_350_threshold/ENSG00000149295'
print(path)

/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/triads_350_threshold/ENSG00000149295


In [315]:
ens_diff_path = os.path.join(path, 'ens_diff_bins.json')
shortest_ens_path = os.path.join(path, 'shortest_ens_bins.json')
jsd_path = os.path.join(path, 'jsd_bins.json')

In [327]:
ens_diff_bin = json.load(open(ens_diff_path, 'r'))['bins']
jsd_bin = json.load(open(jsd_path, 'r'))['bins']
shortest_ens_bin = json.load(open(shortest_ens_path, 'r'))['bins']

In [346]:
ens_diff_edbin = [
    info['triads_info_big_tree']['ens_difference']
    for _, info in ens_diff_bin.items() 
    if info is not None and 'triads_info_big_tree' in info and 'ens_difference' in info['triads_info_big_tree']
]
shortest_ens_edbin = [
    info['triads_info_big_tree']['shortest_ingroup_ens']
    for _, info in ens_diff_bin.items() 
    if info is not None and 'triads_info_big_tree' in info and 'shortest_ingroup_ens' in info['triads_info_big_tree']
]

jsds_edbin = [
    info['triads_info_big_tree']['jsd_dict']['Ingroup_JSD']
    for _, info in ens_diff_bin.items() if info is not None
]


In [348]:
ens_diff_jsdbin = [
    info['triads_info_big_tree']['ens_difference']
    for _, info in jsd_bin.items() 
    if info is not None and 'triads_info_big_tree' in info and 'ens_difference' in info['triads_info_big_tree']
]
jsds_jsdbin = [
    info['triads_info_big_tree']['jsd_dict']['Ingroup_JSD']
    for _, info in jsd_bin.items()  if info is not None
]
shortest_ens_jsdbin = [
    info['triads_info_big_tree']['shortest_ingroup_ens']
    for _, info in jsd_bin.items() 
    if info is not None and 'triads_info_big_tree' in info and 'shortest_ingroup_ens' in info['triads_info_big_tree']
]

In [349]:
ens_diff_sebin = [
    info['triads_info_big_tree']['ens_difference']
    for _, info in shortest_ens_bin.items() 
    if info is not None and 'triads_info_big_tree' in info and 'ens_difference' in info['triads_info_big_tree']
]
jsds_sebin = [
    info['triads_info_big_tree']['jsd_dict']['Ingroup_JSD']
    for _, info in shortest_ens_bin.items() if info is not None
]
shortest_ens_sebin = [
    info['triads_info_big_tree']['shortest_ingroup_ens']
    for _, info in shortest_ens_bin.items() 
    if info is not None and 'triads_info_big_tree' in info and 'shortest_ingroup_ens' in info['triads_info_big_tree']
]

In [353]:

indices_ens_diff = list(range(1, len(ens_diff_edbin) + 1))
indices_jsd = list(range(1, len(jsds_edbin) + 1))
indices_shorest_ens = list(range(1, len(shortest_ens_edbin) + 1))


# Create the scatter plot
fig1 = go.Figure()

# Add ENS Differences scatter plot
fig1.add_trace(go.Scatter(
    x=indices_ens_diff, y=ens_diff_edbin, mode='markers',
    marker=dict(size=10), name='ENS Differences'))

# Add JSD scatter plot
fig1.add_trace(go.Scatter(
    x=indices_jsd, y=jsds_edbin, mode='markers',
    marker=dict(size=10), name='JSD'))

# Add Shortest ENS scatter plot
fig1.add_trace(go.Scatter(
    x=indices_shorest_ens, y=shortest_ens_edbin, mode='markers',
    marker=dict(size=10), name='Shortest ENS'))

# Update layout for clear visualization
fig1.update_layout(
    title='Uniform distirbution of each property',
    xaxis_title='Index',
    yaxis_title='Values',
    showlegend=True,
    
)

fig1.show()

In [65]:
sorted_data = np.sort(ens_diff_edbin)

n = len(sorted_data)
empirical_quantiles = [(i - 0.5) / n for i in range(1, n + 1)]
theoretical_quantiles = stats.uniform.ppf(empirical_quantiles, loc=np.min(ens_diff_edbin), scale=np.max(ens_diff_edbin) - np.min(ens_diff_edbin))


In [66]:

n = len(ens_diff_edbin)
empirical_quantiles = [(i - 0.5) / n for i in range(1, n + 1)]
theoretical_quantiles = stats.uniform.ppf(empirical_quantiles, loc=np.min(ens_diff_edbin), scale=np.max(ens_diff_edbin) - np.min(ens_diff_edbin))

# Define the range for the 45-degree line
x_line = np.linspace(np.min(theoretical_quantiles), np.max(theoretical_quantiles), 500)

# Create the QQ plot with a 45-degree line
fig = go.Figure()
fig.add_trace(go.Scatter(x=theoretical_quantiles, y=ens_diff_edbin, mode='markers', name='Data Points'))
fig.add_trace(go.Scatter(x=x_line, y=x_line, mode='lines', name='45-degree Line', line=dict(color='red')))

fig.update_layout(
    title='QQ Plot: Empirical vs. Theoretical Quantiles - ens_differences',
    xaxis_title='Theoretical Quantiles (Uniform Distribution)',
    yaxis_title='Empirical Quantiles of ENS Differences',
    showlegend=True
)

fig.show()

In [67]:
n = len(jsds_jsdbin)
empirical_quantiles = [(i - 0.5) / n for i in range(1, n + 1)]
theoretical_quantiles = stats.uniform.ppf(empirical_quantiles, loc=np.min(jsds_jsdbin), scale=np.max(jsds_jsdbin) - np.min(jsds_jsdbin))

# Define the range for the 45-degree line
x_line = np.linspace(np.min(theoretical_quantiles), np.max(theoretical_quantiles), 500)

# Create the QQ plot with a 45-degree line
fig = go.Figure()
fig.add_trace(go.Scatter(x=theoretical_quantiles, y=jsds_jsdbin, mode='markers', name='Data Points'))
fig.add_trace(go.Scatter(x=x_line, y=x_line, mode='lines', name='45-degree Line', line=dict(color='red')))

fig.update_layout(
    title='QQ Plot: Empirical vs. Theoretical Quantiles - jsd',
    xaxis_title='Theoretical Quantiles (Uniform Distribution)',
    yaxis_title='Empirical Quantiles of ENS Differences',
    showlegend=True
)

fig.show()

In [68]:

n = len(shortest_ens_sebin)
empirical_quantiles = [(i - 0.5) / n for i in range(1, n + 1)]
theoretical_quantiles = stats.uniform.ppf(empirical_quantiles, loc=np.min(shortest_ens_sebin), scale=np.max(shortest_ens_sebin) - np.min(shortest_ens_sebin))

# Define the range for the 45-degree line
x_line = np.linspace(np.min(theoretical_quantiles), np.max(theoretical_quantiles), 500)

# Create the QQ plot with a 45-degree line
fig = go.Figure()
fig.add_trace(go.Scatter(x=theoretical_quantiles, y=shortest_ens_sebin, mode='markers', name='Data Points'))
fig.add_trace(go.Scatter(x=x_line, y=x_line, mode='lines', name='45-degree Line', line=dict(color='red')))

fig.update_layout(
    title='QQ Plot: Empirical vs. Theoretical Quantiles - shortest_ens',
    xaxis_title='Theoretical Quantiles (Uniform Distribution)',
    yaxis_title='Empirical Quantiles of ENS Differences',
    showlegend=True
)

fig.show()

## Correlation in real data relateds to JSD

In [160]:


# # Extract pairs from one of the bins (choose the appropriate one)
# pairs_ens_diff_bin = extract_pairs(ens_diff_bin) 
# pairs_jsd_bin = extract_pairs(jsd_bin) 

# pairs_shorest_ens_bin = extract_pairs(shortest_ens_bin)  

# pairs_ens_diff_jsd = pairs_ens_diff_bin + pairs_jsd_bin + pairs_shorest_ens_bin

# Separate the pairs into x and y lists for plotting
# all_ens_diff, all_jsd = zip(*pairs_ens_diff_jsd)  # This unpacks the pairs into two lists

# Create the scatter plot
# fig = go.Figure(data=go.Scatter(x=all_jsd, y=all_ens_diff, mode='markers'))
# fig.update_layout(
#     title='Scatter Plot of ENS Differences vs. Ingroup JSD',
#     yaxis_title='ENS Difference',
#     xaxis_title='Ingroup JSD',
#     showlegend=False
# )

# fig.show()
# corr, p_value = stats.pearsonr(all_jsd, all_ens_diff)
# corr, p_value

In [161]:
ancester_distirbution_dict = json.load(open('/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/triads_350_threshold/internal_root_distributions.json', 'r'))

In [162]:
information_dict = {}
for gene_id, distirbutions_info in ancester_distirbution_dict.items():
    information_dict[gene_id] = {}
    for identifier, distirbution in distirbutions_info.items():
        information_dict[gene_id][identifier] = calculate_information(distirbution)

In [163]:
information_list = [value for gene_id in information_dict for value in information_dict[gene_id].values()]
np.max(information_list)

0.604653799594729

In [164]:
average_information_dict = {}
for gene, informations in information_dict.items():
    average_information_dict[gene] = np.average(list(informations.values()))

In [299]:
# Example usage
root_directory = '/Users/gulugulu/Desktop/honours/data_local/whole_genome_mammal87/triads_350_threshold'
paths_gene_folder = find_subdirectory_paths(root_directory)

In [303]:
def remove_outliers_iqr(data1, data2):
    def compute_iqr_bounds(data):
        Q1 = np.percentile(data, 25)
        Q3 = np.percentile(data, 75)
        IQR = Q3 - Q1
        lower_bound = Q1 - 1.5 * IQR
        upper_bound = Q3 + 1.5 * IQR
        return lower_bound, upper_bound

    # Calculate IQR bounds for both lists
    lower_bound1, upper_bound1 = compute_iqr_bounds(data1)
    lower_bound2, upper_bound2 = compute_iqr_bounds(data2)

    # Filter out pairs where either value is an outlier
    filtered_data1 = []
    filtered_data2 = []

    for val1, val2 in zip(data1, data2):
        if (lower_bound1 <= val1 <= upper_bound1) and (lower_bound2 <= val2 <= upper_bound2):
            filtered_data1.append(val1)
            filtered_data2.append(val2)

    return filtered_data1, filtered_data2

def extract_pairs(bins):
    pairs = []
    for key, value in bins.items():
        if value and 'triads_info_big_tree' in value:  # Check if the value and 'triads_info' exist
            ens_difference = value['triads_info_big_tree'].get('ens_difference')
            jsd_dict = value['triads_info_big_tree'].get('jsd_dict')
            ingroup_jsd = jsd_dict['Ingroup_JSD']
            JSD_difference = jsd_dict.get('JSD_difference')
            jsd_diff = abs(list(JSD_difference.values())[0]- list(JSD_difference.values())[1])
            if ens_difference is not None and jsd_diff is not None:
                pairs.append((ens_difference, jsd_diff))
    return pairs

def get_ens_diff_and_jsd(paths):
    all_ens_diff_jsd_dict = {}
    for gene_name, path in paths.items():
        ens_diff_path = os.path.join(path, 'ens_diff_bins.json')
        shortest_ens_path = os.path.join(path, 'shortest_ens_bins.json')
        jsd_path = os.path.join(path, 'jsd_bins.json')

        ens_diff_bin = json.load(open(ens_diff_path, 'r'))['bins']
        jsd_bin = json.load(open(jsd_path, 'r'))['bins']
        shortest_ens_bin = json.load(open(shortest_ens_path, 'r'))['bins']

        # Extract pairs from one of the bins (choose the appropriate one)
        pairs_ens_diff_bin = extract_pairs(ens_diff_bin) 
        pairs_jsd_bin = extract_pairs(jsd_bin) 

        pairs_shorest_ens_bin = extract_pairs(shortest_ens_bin)  

        pairs_ens_diff_jsd = pairs_ens_diff_bin + pairs_jsd_bin + pairs_shorest_ens_bin


        # Separate the pairs into x and y lists for plotting
        all_ens_diff, all_jsd = zip(*pairs_ens_diff_jsd)  # This unpacks the pairs into two lists
        all_ens_diff_filtered, all_jsd_filtered = remove_outliers_iqr(np.array(all_ens_diff), np.array(all_jsd))
        all_ens_diff_jsd_dict[gene_name] = {'all_ens_diff': all_ens_diff_filtered, 'all_jsd': all_jsd_filtered}
    
    return all_ens_diff_jsd_dict



In [304]:
all_ens_diff_and_jsd = get_ens_diff_and_jsd(paths_gene_folder)

In [305]:
corr_p_value_dict = {}
for gene_name, values in all_ens_diff_and_jsd.items():
    cor, p_value = stats.pearsonr(np.sqrt(values['all_ens_diff']), np.sqrt(values['all_jsd']))
    corr_p_value_dict[gene_name] = {'correlation_factor': cor, 'p_value': p_value}
        

In [308]:
import plotly.express as px
corr_dict = {gene: corr_p_value_dict[gene]['correlation_factor'] for gene in average_information_dict.keys()}
information_correlation_fig = px.scatter(x = list(average_information_dict.values()), y = list(corr_dict.values()), labels={'x':'Information (Average)', 'y':'Correlation Coefficient'}, trendline="ols", title= None)
# Update layout with labels and title
information_correlation_fig.update_layout(
    template='plotly_white',
    margin=dict(l=20, r=20, t=50, b=20),
    autosize=True,
    yaxis_title_font={'size': 20},  
    xaxis_title_font={'size': 20}, 
    width=None 
)
information_correlation_fig.show()



In [309]:
# Preparing data for plotting
gene_names = list(corr_p_value_dict.keys())
correlation_factors = [corr_p_value_dict[gene]['correlation_factor'] for gene in gene_names]
p_values = [corr_p_value_dict[gene]['p_value'] for gene in gene_names]

# Create the bar chart
fig = go.Figure(go.Bar(
    x=correlation_factors,
    y=gene_names,
    orientation='h',  # Horizontal bar chart
    marker=dict(color=correlation_factors, coloraxis="coloraxis")  # Color based on the correlation factor
))
fig.add_shape(
    type="line",
    x0=0.2, y0=0, x1=0.2, y1=len(gene_names),
    line=dict(color="yellow", width=3, dash="dashdot"),
)

# Update layout for better visualization
fig.update_layout(
    title="Correlation Factors between In-group ENS_diff and JSD_diff",
    xaxis_title="Correlation Factor",
    yaxis_title="Gene ID",
    coloraxis=dict(colorscale='Bluered_r'),  # Red for higher, blue for lower values
    height=1200  # Adjust height based on the number of genes to avoid squeezing
)

fig.show()

In [313]:
count = len([x for x in p_values if x < 0.0003])
count

84

In [312]:
count2 = len([x for x in correlation_factors if x > 0.2])
count2

89

In [288]:

def plot_gene_data(all_ens_diff_jsd_dict):
    keys = list(all_ens_diff_jsd_dict.keys())
    rows = int(len(keys) ** 0.5) + 1  # Calculate the number of rows for subplots
    cols = (len(keys) + rows - 1) // rows  # Calculate the number of columns

    fig = make_subplots(rows=rows, cols=cols, subplot_titles=[f'{key}' for key in keys])
    
    # Populate subplots
    for index, key in enumerate(keys, start=1):
        gene_data = all_ens_diff_jsd_dict[key]
        all_ens_diff = gene_data['all_ens_diff']
        all_jsd = gene_data['all_jsd']

        row = (index - 1) // cols + 1
        col = (index - 1) % cols + 1
        
        fig.add_trace(
            go.Scatter(
                x=np.sqrt(all_jsd),
                y=np.sqrt(all_ens_diff),
                mode='markers'
            ),
            row=row,
            col=col
        )

        # Adding a trend line
        fig.add_trace(
            go.Scatter(
                x=np.sqrt(all_jsd),
                y=np.poly1d(np.polyfit(np.sqrt(all_jsd), np.sqrt(all_ens_diff), 1))(np.sqrt(all_jsd)),
                mode='lines',
                name=f'Trend {key}',
                line=dict(color='red')
            ),
            row=row,
            col=col
        )
        # Update axis properties
        fig.update_xaxes(title_text="Ingroup JSD" if row == rows else "", row=row, col=col)
        fig.update_yaxes(title_text="ENS Difference" if col == 1 else "", row=row, col=col)
    
    fig.update_layout(
        height=300 * rows,  # Set a reasonable height based on the number of rows
        width=300 * cols,   # Set a reasonable width based on the number of columns
        title_text="Scatter Plots of ENS Differences vs. Ingroup JSD",
        showlegend=False
    )
    
    return fig

# Usage example
# Assume all_ens_diff_jsd_dict is defined with your data
fig = plot_gene_data(all_ens_diff_and_jsd)
fig.show()

In [289]:
# path = 
# ens_diff_path = os.path.join(path, 'ens_diff_bins.json')
# shortest_ens_path = os.path.join(path, 'shortest_ens_bins.json')
# jsd_path = os.path.join(path, 'jsd_bins.json')

# ens_diff_bin = json.load(open(ens_diff_path, 'r'))['bins']
# jsd_bin = json.load(open(jsd_path, 'r'))['bins']
# shortest_ens_bin = json.load(open(shortest_ens_path, 'r'))['bins']

# # Extract pairs from one of the bins (choose the appropriate one)
# pairs_ens_diff_bin = extract_pairs(ens_diff_bin) 
# pairs_jsd_bin = extract_pairs(jsd_bin) 

# pairs_shorest_ens_bin = extract_pairs(shortest_ens_bin)  

# pairs_ens_diff_jsd = pairs_ens_diff_bin + pairs_jsd_bin + pairs_shorest_ens_bin

# # Separate the pairs into x and y lists for plotting
# all_ens_diff, all_jsd = zip(*pairs_ens_diff_jsd)  # This unpacks the pairs into two lists

In [290]:
nabla_ens_log_ratio_fig = px.scatter(x = np.sqrt(all_ens_diff_and_jsd['ENSG00000187151']['all_jsd']), y = np.sqrt(all_ens_diff_and_jsd['ENSG00000187151']['all_ens_diff']), labels={'x':'jsd', 'y':'ens_diff'}, trendline="ols", title= None)
# Update layout with labels and title
nabla_ens_log_ratio_fig.update_layout(
    template='plotly_white',
    margin=dict(l=20, r=20, t=50, b=20),
    autosize=True,
    yaxis_title_font={'size': 20},  
    xaxis_title_font={'size': 20}, 
    width=None 
)
nabla_ens_log_ratio_fig.show()

In [291]:
re = px.get_trendline_results(nabla_ens_log_ratio_fig)
re.px_fit_results.iloc[0].summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:                      y   R-squared:                       0.373
Model:                            OLS   Adj. R-squared:                  0.370
Method:                 Least Squares   F-statistic:                     135.0
Date:                Wed, 07 Aug 2024   Prob (F-statistic):           8.52e-25
Time:                        11:27:06   Log-Likelihood:                 231.53
No. Observations:                 229   AIC:                            -459.1
Df Residuals:                     227   BIC:                            -452.2
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
==============================================================================
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const          0.1272      0.011     11.443      0.000       0.105       0.149
x1             2.8052      0.241     11.619      0.000       2.329       3.281
==============================================================================
Omnibus:                       15.706   Durbin-Watson:                   0.962
Prob(Omnibus):                  0.000   Jarque-Bera (JB):               17.116
Skew:                           0.646   Prob(JB):                     0.000192
Kurtosis:                       2.647   Cond. No.                         41.4
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
"""

In [292]:
import statsmodels.api as sm
import pandas as pd

data = {
    'jsd': np.sqrt(all_ens_diff_and_jsd['ENSG00000187151']['all_jsd']),  # Jensen-Shannon divergence values
    'ens_diff': np.sqrt(all_ens_diff_and_jsd['ENSG00000187151']['all_ens_diff'])  # Ensemble difference values
}
df = pd.DataFrame(data)
X = sm.add_constant(df['jsd'])
y = df['ens_diff']
model = sm.OLS(y, X).fit()
print(model.summary())

                            OLS Regression Results                            
Dep. Variable:               ens_diff   R-squared:                       0.373
Model:                            OLS   Adj. R-squared:                  0.370
Method:                 Least Squares   F-statistic:                     135.0
Date:                Wed, 07 Aug 2024   Prob (F-statistic):           8.52e-25
Time:                        11:27:06   Log-Likelihood:                 231.53
No. Observations:                 229   AIC:                            -459.1
Df Residuals:                     227   BIC:                            -452.2
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const          0.1272      0.011     11.443      0.0

In [293]:
a = np.sqrt(all_ens_diff_and_jsd['ENSG00000187151']['all_ens_diff'])
px.histogram(a)

In [2]:
from cogent3 import available_models
available_models()

Specify a model using 'Abbreviation' (case sensitive).
================================================================================================================================================================================================================================================================================================================================================
Model Type    Abbreviation      Description                                                                                                                                                                                                                                                                                                     
------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
nucleotide    BH                Barry and Hartigan Discrete Time substitution model Barry and Hartigan 1987. Biometrics 43: 261–76.                                                                                                                                                                                                             
nucleotide    DT                Discrete Time substitution model (non-stationary, non-reversible). motif_length=2 makes this a dinucleotide model, motif_length=3 a trinucleotide model.                                                                                                                                                        
nucleotide    GN                General Markov Nucleotide (non-stationary, non-reversible). Kaehler, Yap, Zhang, Huttley, 2015, Sys Biol 64 (2): 281–93                                                                                                                                                                                         
nucleotide    ssGN              strand-symmetric general Markov nucleotide (non-stationary, non-reversible). Kaehler, 2017, Journal of Theoretical Biology 420: 144–51                                                                                                                                                                          
nucleotide    K80               Kimura 1980                                                                                                                                                                                                                                                                                                     
nucleotide    JC69              Jukes and Cantor's 1969 model                                                                                                                                                                                                                                                                                   
nucleotide    GTR               General Time Reversible nucleotide substitution model.                                                                                                                                                                                                                                                          
nucleotide    TN93              Tamura and Nei 1993 model                                                                                                                                                                                                                                                                                       
nucleotide    HKY85             Hasegawa, Kishino and Yano 1985 model                                                                                                                                                                         